In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train = pd.read_csv('../../Feature_Encoding/data/train_js_encoding.csv')
df_test = pd.read_csv('../../Feature_Encoding/data/test_js_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train, x_validation, y_train, y_validation = model_selection.train_test_split(df_train, y, test_size=0.3, stratify=y)

In [8]:
catboost_2 = catboost2(x_train, y_train, x_validation, y_validation)
test_model(catboost_2, x_validation, y_validation)
cross_val(catboost_2, x_train, y_train)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.6697318	total: 50.5ms	remaining: 15.6s
1:	learn: 0.6607799	total: 52.7ms	remaining: 8.12s
2:	learn: 0.6326309	total: 56.9ms	remaining: 5.82s
3:	learn: 0.5886744	total: 64.3ms	remaining: 4.92s
4:	learn: 0.5451229	total: 67ms	remaining: 4.09s
5:	learn: 0.5376298	total: 69.9ms	remaining: 3.54s
6:	learn: 0.4881025	total: 74.5ms	remaining: 3.22s
7:	learn: 0.4825395	total: 77.9ms	remaining: 2.94s
8:	learn: 0.4467911	total: 82.1ms	remaining: 2.75s
9:	learn: 0.4384798	total: 85.3ms	remaining: 2.56s
10:	learn: 0.4102906	total: 88.9ms	remaining: 2.42s
11:	learn: 0.3951456	total: 92.9ms	remaining: 2.31s
12:	learn: 0.3939467	total: 97.2ms	remaining: 2.22s
13:	learn: 0.3873978	total: 101ms	remaining: 2.13s
14:	learn: 0.3796072	total: 104ms	remaining: 2.05s
15:	learn: 0.3758594	total: 107ms	remaining: 1.97s
16:	learn: 0.3652835	total: 111ms	remaining: 1.91s
17:	learn: 0.3573758	total: 115ms	remaining: 1.87s
18:	learn: 0.35735

204:	learn: 0.1924659	total: 757ms	remaining: 388ms
205:	learn: 0.1923836	total: 760ms	remaining: 384ms
206:	learn: 0.1911909	total: 764ms	remaining: 380ms
207:	learn: 0.1901222	total: 768ms	remaining: 376ms
208:	learn: 0.1900995	total: 771ms	remaining: 373ms
209:	learn: 0.1900993	total: 773ms	remaining: 368ms
210:	learn: 0.1900993	total: 777ms	remaining: 364ms
211:	learn: 0.1900716	total: 779ms	remaining: 360ms
212:	learn: 0.1896674	total: 781ms	remaining: 356ms
213:	learn: 0.1894730	total: 785ms	remaining: 352ms
214:	learn: 0.1894571	total: 788ms	remaining: 348ms
215:	learn: 0.1889973	total: 793ms	remaining: 345ms
216:	learn: 0.1889754	total: 796ms	remaining: 341ms
217:	learn: 0.1889430	total: 798ms	remaining: 337ms
218:	learn: 0.1884621	total: 802ms	remaining: 333ms
219:	learn: 0.1883720	total: 806ms	remaining: 330ms
220:	learn: 0.1875852	total: 809ms	remaining: 326ms
221:	learn: 0.1860140	total: 812ms	remaining: 322ms
222:	learn: 0.1859076	total: 814ms	remaining: 318ms
223:	learn: 

96:	learn: 0.2229662	total: 385ms	remaining: 846ms
97:	learn: 0.2219305	total: 387ms	remaining: 838ms
98:	learn: 0.2219305	total: 391ms	remaining: 832ms
99:	learn: 0.2219305	total: 392ms	remaining: 824ms
100:	learn: 0.2203131	total: 397ms	remaining: 821ms
101:	learn: 0.2201224	total: 400ms	remaining: 815ms
102:	learn: 0.2197186	total: 403ms	remaining: 810ms
103:	learn: 0.2181369	total: 409ms	remaining: 811ms
104:	learn: 0.2180803	total: 412ms	remaining: 804ms
105:	learn: 0.2164316	total: 415ms	remaining: 798ms
106:	learn: 0.2164316	total: 416ms	remaining: 790ms
107:	learn: 0.2162453	total: 418ms	remaining: 783ms
108:	learn: 0.2161970	total: 422ms	remaining: 779ms
109:	learn: 0.2151842	total: 427ms	remaining: 776ms
110:	learn: 0.2139978	total: 432ms	remaining: 775ms
111:	learn: 0.2135762	total: 435ms	remaining: 769ms
112:	learn: 0.2135762	total: 437ms	remaining: 762ms
113:	learn: 0.2135762	total: 439ms	remaining: 755ms
114:	learn: 0.2133855	total: 444ms	remaining: 753ms
115:	learn: 0.21

305:	learn: 0.1480769	total: 1.16s	remaining: 15.2ms
306:	learn: 0.1474321	total: 1.17s	remaining: 11.4ms
307:	learn: 0.1474321	total: 1.17s	remaining: 7.63ms
308:	learn: 0.1471765	total: 1.18s	remaining: 3.82ms
309:	learn: 0.1471765	total: 1.18s	remaining: 0us
0:	learn: 0.6047083	total: 3.85ms	remaining: 1.74s
1:	learn: 0.5497308	total: 7.96ms	remaining: 1.79s
2:	learn: 0.5203447	total: 15.2ms	remaining: 2.28s
3:	learn: 0.4853476	total: 23.5ms	remaining: 2.63s
4:	learn: 0.4649575	total: 27.3ms	remaining: 2.44s
5:	learn: 0.4401773	total: 30.7ms	remaining: 2.28s
6:	learn: 0.4159980	total: 43.2ms	remaining: 2.75s
7:	learn: 0.4025134	total: 47.9ms	remaining: 2.65s
8:	learn: 0.3935142	total: 52.5ms	remaining: 2.58s
9:	learn: 0.3755012	total: 57.4ms	remaining: 2.54s
10:	learn: 0.3635699	total: 63.6ms	remaining: 2.55s
11:	learn: 0.3498830	total: 68.7ms	remaining: 2.52s
12:	learn: 0.3461862	total: 72ms	remaining: 2.43s
13:	learn: 0.3407689	total: 81.6ms	remaining: 2.55s
14:	learn: 0.3294942	t

185:	learn: 0.1736343	total: 825ms	remaining: 1.18s
186:	learn: 0.1734271	total: 830ms	remaining: 1.18s
187:	learn: 0.1729078	total: 834ms	remaining: 1.17s
188:	learn: 0.1727791	total: 840ms	remaining: 1.17s
189:	learn: 0.1724293	total: 842ms	remaining: 1.16s
190:	learn: 0.1720678	total: 844ms	remaining: 1.15s
191:	learn: 0.1717611	total: 849ms	remaining: 1.15s
192:	learn: 0.1711565	total: 852ms	remaining: 1.14s
193:	learn: 0.1708461	total: 859ms	remaining: 1.14s
194:	learn: 0.1706279	total: 862ms	remaining: 1.14s
195:	learn: 0.1704961	total: 866ms	remaining: 1.13s
196:	learn: 0.1699918	total: 870ms	remaining: 1.13s
197:	learn: 0.1697349	total: 876ms	remaining: 1.12s
198:	learn: 0.1693422	total: 879ms	remaining: 1.12s
199:	learn: 0.1691207	total: 883ms	remaining: 1.11s
200:	learn: 0.1686559	total: 889ms	remaining: 1.11s
201:	learn: 0.1684169	total: 896ms	remaining: 1.11s
202:	learn: 0.1681348	total: 899ms	remaining: 1.1s
203:	learn: 0.1678837	total: 902ms	remaining: 1.1s
204:	learn: 0.

...

184:	learn: 0.0789213	total: 9.06s	remaining: 6.56s
185:	learn: 0.0783818	total: 9.13s	remaining: 6.53s
186:	learn: 0.0779627	total: 9.2s	remaining: 6.5s
187:	learn: 0.0776189	total: 9.29s	remaining: 6.47s
188:	learn: 0.0770699	total: 9.36s	remaining: 6.44s
189:	learn: 0.0761828	total: 9.43s	remaining: 6.4s
190:	learn: 0.0758999	total: 9.48s	remaining: 6.36s
191:	learn: 0.0754951	total: 9.55s	remaining: 6.32s
192:	learn: 0.0751428	total: 9.58s	remaining: 6.25s
193:	learn: 0.0746551	total: 9.63s	remaining: 6.2s
194:	learn: 0.0743622	total: 9.7s	remaining: 6.17s
195:	learn: 0.0741702	total: 9.76s	remaining: 6.12s
196:	learn: 0.0738774	total: 9.86s	remaining: 6.1s
197:	learn: 0.0734959	total: 9.95s	remaining: 6.08s
198:	learn: 0.0729168	total: 10s	remaining: 6.03s
199:	learn: 0.0726078	total: 10.1s	remaining: 6s
200:	learn: 0.0723384	total: 10.1s	remaining: 5.95s
201:	learn: 0.0719699	total: 10.2s	remaining: 5.9s
202:	learn: 0.0717870	total: 10.3s	remaining: 5.86s
203:	learn: 0.0716976	to

26:	learn: 0.2151194	total: 1.25s	remaining: 13.6s
27:	learn: 0.2124463	total: 1.28s	remaining: 13.3s
28:	learn: 0.2101921	total: 1.31s	remaining: 13.1s
29:	learn: 0.2078223	total: 1.38s	remaining: 13.3s
30:	learn: 0.2062827	total: 1.42s	remaining: 13.2s
31:	learn: 0.2035252	total: 1.44s	remaining: 12.9s
32:	learn: 0.2008699	total: 1.52s	remaining: 13.2s
33:	learn: 0.1983945	total: 1.56s	remaining: 13.1s
34:	learn: 0.1955284	total: 1.6s	remaining: 13s
35:	learn: 0.1940489	total: 1.64s	remaining: 12.9s
36:	learn: 0.1918294	total: 1.69s	remaining: 12.9s
37:	learn: 0.1893714	total: 1.73s	remaining: 12.8s
38:	learn: 0.1876322	total: 1.79s	remaining: 12.8s
39:	learn: 0.1857040	total: 1.86s	remaining: 12.9s
40:	learn: 0.1845951	total: 1.95s	remaining: 13.2s
41:	learn: 0.1832657	total: 1.98s	remaining: 13s
42:	learn: 0.1818965	total: 2.02s	remaining: 13s
43:	learn: 0.1799052	total: 2.06s	remaining: 12.9s
44:	learn: 0.1777640	total: 2.13s	remaining: 13s
45:	learn: 0.1762555	total: 2.17s	remain

190:	learn: 0.0689762	total: 9.54s	remaining: 6.39s
191:	learn: 0.0685641	total: 9.58s	remaining: 6.34s
192:	learn: 0.0680403	total: 9.64s	remaining: 6.3s
193:	learn: 0.0675963	total: 9.73s	remaining: 6.27s
194:	learn: 0.0673415	total: 9.79s	remaining: 6.23s
195:	learn: 0.0671954	total: 9.85s	remaining: 6.18s
196:	learn: 0.0670117	total: 9.9s	remaining: 6.13s
197:	learn: 0.0668190	total: 9.94s	remaining: 6.08s
198:	learn: 0.0661557	total: 9.97s	remaining: 6.01s
199:	learn: 0.0655188	total: 10s	remaining: 5.97s
200:	learn: 0.0653146	total: 10.1s	remaining: 5.92s
201:	learn: 0.0651649	total: 10.2s	remaining: 5.88s
202:	learn: 0.0647718	total: 10.2s	remaining: 5.84s
203:	learn: 0.0647703	total: 10.2s	remaining: 5.76s
204:	learn: 0.0642997	total: 10.3s	remaining: 5.72s
205:	learn: 0.0639932	total: 10.4s	remaining: 5.68s
206:	learn: 0.0637724	total: 10.4s	remaining: 5.62s
207:	learn: 0.0636032	total: 10.5s	remaining: 5.6s
208:	learn: 0.0635032	total: 10.5s	remaining: 5.55s
209:	learn: 0.063

32:	learn: 0.2010611	total: 1.38s	remaining: 11.9s
33:	learn: 0.1981435	total: 1.43s	remaining: 11.9s
34:	learn: 0.1963862	total: 1.47s	remaining: 11.9s
35:	learn: 0.1944727	total: 1.51s	remaining: 11.9s
36:	learn: 0.1907761	total: 1.55s	remaining: 11.8s
37:	learn: 0.1881521	total: 1.58s	remaining: 11.7s
38:	learn: 0.1863586	total: 1.63s	remaining: 11.7s
39:	learn: 0.1846475	total: 1.66s	remaining: 11.6s
40:	learn: 0.1834799	total: 1.72s	remaining: 11.7s
41:	learn: 0.1818701	total: 1.75s	remaining: 11.6s
42:	learn: 0.1789902	total: 1.79s	remaining: 11.5s
43:	learn: 0.1769410	total: 1.85s	remaining: 11.5s
44:	learn: 0.1740800	total: 1.89s	remaining: 11.5s
45:	learn: 0.1724811	total: 1.93s	remaining: 11.4s
46:	learn: 0.1709269	total: 1.97s	remaining: 11.4s
47:	learn: 0.1700567	total: 2s	remaining: 11.3s
48:	learn: 0.1676160	total: 2.06s	remaining: 11.3s
49:	learn: 0.1655600	total: 2.08s	remaining: 11.2s
50:	learn: 0.1643173	total: 2.12s	remaining: 11.2s
51:	learn: 0.1631906	total: 2.16s	

194:	learn: 0.0703616	total: 9.35s	remaining: 5.95s
195:	learn: 0.0699631	total: 9.45s	remaining: 5.93s
196:	learn: 0.0697672	total: 9.51s	remaining: 5.89s
197:	learn: 0.0692008	total: 9.57s	remaining: 5.85s
198:	learn: 0.0690993	total: 9.62s	remaining: 5.8s
199:	learn: 0.0687718	total: 9.68s	remaining: 5.76s
200:	learn: 0.0685235	total: 9.73s	remaining: 5.71s
201:	learn: 0.0684087	total: 9.76s	remaining: 5.65s
202:	learn: 0.0680230	total: 9.81s	remaining: 5.61s
203:	learn: 0.0677383	total: 9.86s	remaining: 5.56s
204:	learn: 0.0674425	total: 9.9s	remaining: 5.5s
205:	learn: 0.0669478	total: 9.94s	remaining: 5.45s
206:	learn: 0.0667601	total: 10s	remaining: 5.43s
207:	learn: 0.0664409	total: 10.2s	remaining: 5.43s
208:	learn: 0.0661231	total: 10.3s	remaining: 5.39s
209:	learn: 0.0659214	total: 10.3s	remaining: 5.36s
210:	learn: 0.0657669	total: 10.4s	remaining: 5.32s
211:	learn: 0.0655448	total: 10.4s	remaining: 5.27s
212:	learn: 0.0651976	total: 10.5s	remaining: 5.21s
213:	learn: 0.064

In [9]:
y_pred = catboost_2.predict_proba(df_test)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/js_catboost.csv', index=False)